In [1]:
from pyspark.sql import SparkSession

spark = SparkSession.builder \
    .config("spark.executor.memory", "1g")\
        .config("spark.driver.memory", "4g")\
.appName('VIZ') \
 .master("local[*]")\
    .getOrCreate()

In [2]:
from sedona.spark import *

In [4]:
SedonaContext.create(spark)

In [5]:
import folium
import pandas as pd
import geopandas as gpd
from folium import plugins
from folium.features import DivIcon


In [6]:
def add_marker_to_map(df_pd,m,lat_col,long_col,tooltip=None,popup=None,color="blue"):
  for _, row in df_pd.iterrows():
    folium.Marker(
      location = [row[lat_col],row[long_col]],
      tooltip = tooltip,
      popup = popup(row),
      icon=folium.Icon(color=color,icon="info-sign")
    ).add_to(m)
def add_polygon_to_map(df_pd,m,wkt_column,opacity=0.01,line_weight=0.01,color=None): 
  
    df_pd["polygon"] = gpd.GeoSeries.from_wkt(df_pd[wkt_column])
    geo_data = gpd.GeoDataFrame(df_pd,geometry="polygon")
    for _,row in  geo_data.iterrows():
      sim_geo = gpd.GeoSeries(row["polygon"]).simplify(tolerance=0.0001)
      geo_j = sim_geo.to_json()
      geo_j= folium.GeoJson(data=geo_j,
                               style_function=lambda x: {'fillColor': color,
                                                        'fillOpacity': opacity,
                                                        'color':color,
                                                            "weight": line_weight}
                           )
      geo_j.add_to(m)
def add_circle_to_map(df_pd,m,lat_col,long_col,tooltip=None,popup=None,color="blue"):
  for _, row in df_pd.iterrows():
    folium.CircleMarker(
      location = [row[lat_col],row[long_col]],
      radius=5,
      color=color,
      popup = popup(row)
    ).add_to(m)          
    

def add_marker_to_map(df_pd,m,lat_col,long_col,tooltip=None,popup=None,color="blue"):
  for _, row in df_pd.iterrows():
    folium.Marker(
      location = [row[lat_col],row[long_col]],
      tooltip = tooltip,
      popup = popup(row),
      icon=folium.Icon(color=color,icon="info-sign")
    ).add_to(m)
def add_polygon_to_map(df_pd,m,wkt_column,opacity=0.01,line_weight=0.01,color=None): 
  
    df_pd["polygon"] = gpd.GeoSeries.from_wkt(df_pd[wkt_column])
    geo_data = gpd.GeoDataFrame(df_pd,geometry="polygon")
    for _,row in  geo_data.iterrows():
      sim_geo = gpd.GeoSeries(row["polygon"]).simplify(tolerance=0.0001)
      geo_j = sim_geo.to_json()
      geo_j= folium.GeoJson(data=geo_j,
                               style_function=lambda x: {'fillColor': color,
                                                        'fillOpacity': opacity,
                                                        'color':color,
                                                            "weight": line_weight}
                           )
      geo_j.add_to(m)
def add_circle_to_map(df_pd,m,lat_col,long_col,color="blue"):
  for _, row in df_pd.iterrows():
    folium.CircleMarker(
      location = [row[lat_col],row[long_col]],
      radius=5,
      color=color
    ).add_to(m)

In [111]:
points_in_range_from_polygon = spark.read.parquet("C:\\projects\\h3xwrapper\\data\\test\\POINTS_IN_RANGE_FROM_POLYGON").drop("zc_shape").toPandas()

In [113]:
m = folium.Map()

In [114]:

add_polygon_to_map(points_in_range_from_polygon,m,"polygon_buffer",color="blue",opacity=0.1,line_weight=0.1)

In [115]:

add_polygon_to_map(points_in_range_from_polygon,m,"zc_shape_wkt",color="red",opacity=1,line_weight=0.1)

In [119]:

add_polygon_to_map(points_in_range_from_polygon,m,"h3_index_shape",color="red",opacity=2,line_weight=0.1)

In [118]:
m

In [18]:
zipcodes_shapes = spark.read.parquet("C:\projects\h3xwrapper\data\ZIP_CODE_SHAPES_TEST").toPandas()
block_grupus_shapes = spark.read.parquet("C:\projects\h3xwrapper\data\BLOCK_GROUP_SHAPES_TEST").toPandas()
pois = spark.read.parquet("C:\projects\h3xwrapper\data\POI_TEST").toPandas()

In [21]:
m = folium.Map()
add_polygon_to_map(zipcodes_shapes,m,"zc_shape_wkt",color="red",opacity=0.4,line_weight=3)
add_circle_to_map(pois,m,"lat","long")
add_polygon_to_map(block_grupus_shapes,m,"bg_shape_wkt",color="blue",opacity=0.4,line_weight=3)
m

In [22]:
m.save("./TEST_DATA_VIZ.html")

In [26]:
zc_polygon = spark.read.parquet("C:\projects\h3xwrapper\data\POLYGON_BOUNDARY").toPandas()

In [27]:
m = folium.Map()
add_polygon_to_map(zc_polygon,m,"h3_boundary_shape",color="red",opacity=0.4,line_weight=3)
add_polygon_to_map(zc_polygon,m,"zc_shape_wkt",color="blue",opacity=0.01,line_weight=1)
m

In [30]:
bg_shape = spark.read.parquet("C:\projects\h3xwrapper\data\\test\FILL").select("bg_shape_wkt","h3_shape").toPandas()

In [19]:
bg_shape.printSchema()

root
 |-- bg_id: string (nullable = true)
 |-- bg_shape: geometry (nullable = true)
 |-- row_number: integer (nullable = true)
 |-- h3_cells: long (nullable = true)
 |-- h3_shape: string (nullable = true)
 |-- bg_shape_wkt: string (nullable = true)



In [31]:
h3_shapes = h3_fill.select("h3_shape").toPandas()

NameError: name 'h3_fill' is not defined

In [32]:
m = folium.Map()

In [33]:
add_polygon_to_map(bg_shape,m,"h3_shape",color="red",opacity=0.4,line_weight=3)

In [34]:
add_polygon_to_map(bg_shape,m,"bg_shape_wkt",color="blue",opacity=0.5,line_weight=1)

In [35]:
m

In [30]:
m.save("./NOT_FULL_RES_11.html")

In [4]:
from sedona.maps.SedonaKepler import SedonaKepler

In [14]:
sedona_df_bg =spark.createDataFrame( spark.read.parquet("C:\projects\h3xwrapper\data\INTERSECTED").select("bg_shape").toPandas()[0:1])

In [8]:
sedona_df_zc =spark.createDataFrame( spark.read.parquet("C:\projects\h3xwrapper\data\INTERSECTED").select("zc_shape").toPandas()[0:1])

In [10]:
sedona_df_zc.show()

+--------------------+
|            zc_shape|
+--------------------+
|POLYGON ((-88.247...|
+--------------------+



In [12]:
map=SedonaKepler.create_map(sedona_df_zc.select("zc_shape"),"zc")

User Guide: https://docs.kepler.gl/docs/keplergl-jupyter


In [15]:
SedonaKepler.add_df(map,sedona_df_bg.select("bg_shape"))

In [16]:
map.save_to_html()

Map saved to keplergl_map.html!
